In [104]:
#                                 CHAPMAN UNIVERSITY, CADS
#                                     ERIC ADAMS
#                           CS 770 Big Data Analytic Final Project

import argparse
from uuid import uuid4
from six.moves import input
from confluent_kafka import Producer
from confluent_kafka.serialization import StringSerializer, SerializationContext, MessageField
from confluent_kafka.schema_registry import SchemaRegistryClient
from confluent_kafka.schema_registry.json_schema import JSONSerializer
#from confluent_kafka.schema_registry import *
import pandas as pd
from typing import List


FILE_PATH = "C:\\Users\\Eric\\Desktop\\CHAPMAN\\Chapman Fall 2022\\CS 770 -02\\PROJECT\\kafka_producer\\car_dataset.csv"
columns=['car_name', 'brand', 'model', 'vehicle_age', 'km_driven', 'seller_type',
       'fuel_type', 'transmission_type', 'mileage', 'engine', 'max_power',
       'seats', 'selling_price']


API_KEY = 'FBKVWXHGRKRVK4HN'
SCHEMA_URL  = 'https://psrc-mw0d1.us-east-2.aws.confluent.cloud'
SECRET_KEY = 'IEcIG65g1CKPZjel7des4oUdQZyrVND2/UT7NIOika0LX/TYPq8jX3jS75JkpwJY'
SERVER = 'pkc-ymrq7.us-east-2.aws.confluent.cloud:9092'
PROTOCOL = 'SASL_SSL'
SECURITY_MECHANISM = 'PLAIN'  # security mechanism
SCHEMA_REGISTRY_KEY = 'VIFWWNHLEVOI4YRE'
SCHEMA_REGISTRY_SECRET = '5oTvgOnnVMxyQz8HM98qIS/KD8Wd3XpPLIVOUMno3wwPhEccQfLqrFwXQEvrC8H6'


def set_kafka_conf():
    set_kafka_conf = {"sasl.mechanism":SECURITY_MECHANISM,
                      "bootstrap.servers":BOOTSTRAP_SERVER,
                      "security.protocol": PROTOCOL,
                      "sasl.username":API_KEY,
                      "sasl.password":SECRET_KEY       
                      }
    return set_kafka_conf

def schema_registry_configuration():
    return {"url": SCHEMA_URL,
    'basic.auth.user.info':f"{SCHEMA_REGISTRY_KEY}:{SCHEMA_REGISTRY_SECRET}"
    }


class Vehecle:
    def __init__(self,message:dict):
        for a,b in message.items():
            setattr(self,a,b)
            
            self.message=message
    @staticmethod
    def serialize(record:dict,ctx):
        return Vehecle(message=data)
    def __str__(self):
        return f"{self.message}"
    
    
def read_parameter(file_path):
    df=pd.read_csv(file_path)
    df=df.iloc[:,1:]
    vehecles:List[Vehecle]=[]
    for data in df.values:
        vehecle=Vehecle(dict(zip(columns,data)))
        vehecles.append(vehecle)
        yield vehecle
        
        
def serialize(vehecle:Vehecle, ctx):
    return vehecle.message


def delivery_report(notification, record):
    if notification is not None:
        print((record.key(),notification))
        return
    print(record.key(),record.topic(),record.partition(), record.offset())
    
    
    
    
def  main(topic):
    string_schema= """
    {
  "$id": "http://example.com/myURI.schema.json",
  "$schema": "http://json-schema.org/draft-07/schema#",
  "additionalProperties": false,
  "description": "Sample schema to help you get started.",
  "properties": {
    "brand": {
      "description": "The type(v) type is used.",
      "type": "string"
    },
    "car_name": {
      "description": "The type(v) type is used.",
      "type": "string"
    },
    "engine": {
      "description": "The type(v) type is used.",
      "type": "number"
    },
    "fuel_type": {
      "description": "The type(v) type is used.",
      "type": "string"
    },
    "km_driven": {
      "description": "The type(v) type is used.",
      "type": "number"
    },
    "max_power": {
      "description": "The type(v) type is used.",
      "type": "number"
    },
    "mileage": {
      "description": "The type(v) type is used.",
      "type": "number"
    },
    "model": {
      "description": "The type(v) type is used.",
      "type": "string"
    },
    "seats": {
      "description": "The type(v) type is used.",
      "type": "number"
    },
    "seller_type": {
      "description": "The type(v) type is used.",
      "type": "string"
    },
    "selling_price": {
      "description": "The type(v) type is used.",
      "type": "number"
    },
    "transmission_type": {
      "description": "The type(v) type is used.",
      "type": "string"
    },
    "vehicle_age": {
      "description": "The type(v) type is used.",
      "type": "number"
    }
  },
  "title": "SampleRecord",
  "type": "object"
}
    """
    configuration_schema_reg=schema_registry_configuration()
    schema_client = SchemaRegistryClient(configuration_schema_reg)
    
    serializer = StringSerializer ("utf_8")
    serializer_by_json = JSONSerializer(string_schema, schema_client, serialize)
    
    publisher = Producer(set_kafka_conf())
    print(topic)
    publisher.poll(0.0)
    
    try:
        for vehecle in read_parameter(file_path=FILE_PATH):
            print(vehecle)
            
            publisher.produce(topic=topic,
                              key=serializer(str(uuid4()), serialize),
                              value=serializer_by_json(vehecle,SerializationContext(topic, MessageField.VALUE)),
                              on_delivery=delivery_report)
            
    except KeyboardInterrupt:
        pass
    except ValueError:
        print("bad input, trash record..")
        pass
    print("\nFlushing records..")
    producer.flush()
main("test-topic-1")

test-topic-1
{'car_name': 'Maruti Alto', 'brand': 'Maruti', 'model': 'Alto', 'vehicle_age': 9, 'km_driven': 120000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 19.7, 'engine': 796, 'max_power': 46.3, 'seats': 5, 'selling_price': 120000}
{'car_name': 'Hyundai Grand', 'brand': 'Hyundai', 'model': 'Grand', 'vehicle_age': 5, 'km_driven': 20000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 18.9, 'engine': 1197, 'max_power': 82.0, 'seats': 5, 'selling_price': 550000}
{'car_name': 'Hyundai i20', 'brand': 'Hyundai', 'model': 'i20', 'vehicle_age': 11, 'km_driven': 60000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 17.0, 'engine': 1197, 'max_power': 80.0, 'seats': 5, 'selling_price': 215000}
{'car_name': 'Maruti Alto', 'brand': 'Maruti', 'model': 'Alto', 'vehicle_age': 9, 'km_driven': 37000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'trans

{'car_name': 'Mahindra KUV', 'brand': 'Mahindra', 'model': 'KUV', 'vehicle_age': 5, 'km_driven': 70000, 'seller_type': 'Individual', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 25.32, 'engine': 1198, 'max_power': 77.0, 'seats': 6, 'selling_price': 310000}
{'car_name': 'Mahindra Scorpio', 'brand': 'Mahindra', 'model': 'Scorpio', 'vehicle_age': 4, 'km_driven': 120000, 'seller_type': 'Individual', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 15.4, 'engine': 1997, 'max_power': 120.0, 'seats': 7, 'selling_price': 850000}
{'car_name': 'Hyundai i20', 'brand': 'Hyundai', 'model': 'i20', 'vehicle_age': 8, 'km_driven': 90000, 'seller_type': 'Individual', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 22.54, 'engine': 1396, 'max_power': 88.76, 'seats': 5, 'selling_price': 285000}
{'car_name': 'Maruti Swift Dzire', 'brand': 'Maruti', 'model': 'Swift Dzire', 'vehicle_age': 7, 'km_driven': 120000, 'seller_type': 'Individual', 'fuel_type': 'D

{'car_name': 'Hyundai i20', 'brand': 'Hyundai', 'model': 'i20', 'vehicle_age': 1, 'km_driven': 3700, 'seller_type': 'Trustmark Dealer', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 18.6, 'engine': 1197, 'max_power': 81.86, 'seats': 5, 'selling_price': 765000}
{'car_name': 'Maruti Wagon R', 'brand': 'Maruti', 'model': 'Wagon R', 'vehicle_age': 5, 'km_driven': 25000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 20.51, 'engine': 998, 'max_power': 67.04, 'seats': 5, 'selling_price': 380000}
{'car_name': 'Toyota Fortuner', 'brand': 'Toyota', 'model': 'Fortuner', 'vehicle_age': 4, 'km_driven': 64000, 'seller_type': 'Dealer', 'fuel_type': 'Diesel', 'transmission_type': 'Automatic', 'mileage': 12.9, 'engine': 2755, 'max_power': 174.5, 'seats': 7, 'selling_price': 2625000}
{'car_name': 'Mahindra XUV500', 'brand': 'Mahindra', 'model': 'XUV500', 'vehicle_age': 8, 'km_driven': 50000, 'seller_type': 'Dealer', 'fuel_type': 'Diesel'

{'car_name': 'Hyundai i10', 'brand': 'Hyundai', 'model': 'i10', 'vehicle_age': 12, 'km_driven': 100000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 19.81, 'engine': 1086, 'max_power': 68.05, 'seats': 5, 'selling_price': 215000}
{'car_name': 'Hyundai Verna', 'brand': 'Hyundai', 'model': 'Verna', 'vehicle_age': 11, 'km_driven': 10000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 16.2, 'engine': 1599, 'max_power': 103.2, 'seats': 5, 'selling_price': 370000}
{'car_name': 'Maruti Alto', 'brand': 'Maruti', 'model': 'Alto', 'vehicle_age': 7, 'km_driven': 14971, 'seller_type': 'Trustmark Dealer', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 22.74, 'engine': 796, 'max_power': 47.3, 'seats': 5, 'selling_price': 230000}
{'car_name': 'Honda City', 'brand': 'Honda', 'model': 'City', 'vehicle_age': 2, 'km_driven': 16000, 'seller_type': 'Dealer', 'fuel_type': 'Petrol', 'transmission_

{'car_name': 'Volkswagen Vento', 'brand': 'Volkswagen', 'model': 'Vento', 'vehicle_age': 6, 'km_driven': 67000, 'seller_type': 'Dealer', 'fuel_type': 'Diesel', 'transmission_type': 'Automatic', 'mileage': 22.15, 'engine': 1498, 'max_power': 108.6, 'seats': 5, 'selling_price': 565000}
{'car_name': 'Maruti Celerio', 'brand': 'Maruti', 'model': 'Celerio', 'vehicle_age': 4, 'km_driven': 20000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 23.1, 'engine': 998, 'max_power': 67.04, 'seats': 5, 'selling_price': 450000}
{'car_name': 'Hyundai Creta', 'brand': 'Hyundai', 'model': 'Creta', 'vehicle_age': 2, 'km_driven': 39000, 'seller_type': 'Dealer', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 15.8, 'engine': 1591, 'max_power': 121.3, 'seats': 5, 'selling_price': 920000}
{'car_name': 'Mahindra Scorpio', 'brand': 'Mahindra', 'model': 'Scorpio', 'vehicle_age': 4, 'km_driven': 36000, 'seller_type': 'Dealer', 'fuel_type': 'Diesel', 

...

{'car_name': 'Maruti Baleno', 'brand': 'Maruti', 'model': 'Baleno', 'vehicle_age': 4, 'km_driven': 43318, 'seller_type': 'Dealer', 'fuel_type': 'Petrol', 'transmission_type': 'Automatic', 'mileage': 19.56, 'engine': 1197, 'max_power': 81.8, 'seats': 5, 'selling_price': 750000}
{'car_name': 'Maruti Alto', 'brand': 'Maruti', 'model': 'Alto', 'vehicle_age': 5, 'km_driven': 6800, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 24.7, 'engine': 796, 'max_power': 47.3, 'seats': 5, 'selling_price': 300000}
{'car_name': 'Hyundai Creta', 'brand': 'Hyundai', 'model': 'Creta', 'vehicle_age': 4, 'km_driven': 32000, 'seller_type': 'Dealer', 'fuel_type': 'Petrol', 'transmission_type': 'Automatic', 'mileage': 13.0, 'engine': 1591, 'max_power': 121.3, 'seats': 5, 'selling_price': 1125000}
{'car_name': 'Maruti Alto', 'brand': 'Maruti', 'model': 'Alto', 'vehicle_age': 10, 'km_driven': 32000, 'seller_type': 'Dealer', 'fuel_type': 'Petrol', 'transmission_type':

{'car_name': 'Toyota Innova', 'brand': 'Toyota', 'model': 'Innova', 'vehicle_age': 4, 'km_driven': 43458, 'seller_type': 'Dealer', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 12.99, 'engine': 2494, 'max_power': 100.0, 'seats': 8, 'selling_price': 1670000}
{'car_name': 'Maruti Wagon R', 'brand': 'Maruti', 'model': 'Wagon R', 'vehicle_age': 13, 'km_driven': 80000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 18.9, 'engine': 998, 'max_power': 67.1, 'seats': 5, 'selling_price': 150000}
{'car_name': 'Toyota Innova', 'brand': 'Toyota', 'model': 'Innova', 'vehicle_age': 3, 'km_driven': 38000, 'seller_type': 'Dealer', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 13.68, 'engine': 2393, 'max_power': 147.8, 'seats': 8, 'selling_price': 1991000}
{'car_name': 'Ford Figo', 'brand': 'Ford', 'model': 'Figo', 'vehicle_age': 10, 'km_driven': 75000, 'seller_type': 'Dealer', 'fuel_type': 'Diesel', 'transmission_type'

{'car_name': 'Maruti Swift Dzire', 'brand': 'Maruti', 'model': 'Swift Dzire', 'vehicle_age': 3, 'km_driven': 12000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'transmission_type': 'Automatic', 'mileage': 22.0, 'engine': 1197, 'max_power': 81.8, 'seats': 5, 'selling_price': 800000}
{'car_name': 'Maruti Celerio', 'brand': 'Maruti', 'model': 'Celerio', 'vehicle_age': 2, 'km_driven': 5000, 'seller_type': 'Dealer', 'fuel_type': 'Petrol', 'transmission_type': 'Manual', 'mileage': 23.1, 'engine': 998, 'max_power': 67.04, 'seats': 5, 'selling_price': 440000}
{'car_name': 'Maruti Swift Dzire', 'brand': 'Maruti', 'model': 'Swift Dzire', 'vehicle_age': 7, 'km_driven': 70000, 'seller_type': 'Individual', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 23.4, 'engine': 1248, 'max_power': 74.0, 'seats': 5, 'selling_price': 575000}
{'car_name': 'Toyota Innova', 'brand': 'Toyota', 'model': 'Innova', 'vehicle_age': 2, 'km_driven': 6500, 'seller_type': 'Dealer', 'fuel_type': 'Di

{'car_name': 'Hyundai Verna', 'brand': 'Hyundai', 'model': 'Verna', 'vehicle_age': 5, 'km_driven': 70000, 'seller_type': 'Individual', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 23.9, 'engine': 1582, 'max_power': 126.2, 'seats': 5, 'selling_price': 850000}
{'car_name': 'Tata Safari', 'brand': 'Tata', 'model': 'Safari', 'vehicle_age': 10, 'km_driven': 120000, 'seller_type': 'Individual', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 13.93, 'engine': 2179, 'max_power': 138.0, 'seats': 7, 'selling_price': 250000}
{'car_name': 'Ford Ecosport', 'brand': 'Ford', 'model': 'Ecosport', 'vehicle_age': 6, 'km_driven': 70000, 'seller_type': 'Individual', 'fuel_type': 'Diesel', 'transmission_type': 'Manual', 'mileage': 22.77, 'engine': 1498, 'max_power': 98.59, 'seats': 5, 'selling_price': 740000}
{'car_name': 'Ford Ecosport', 'brand': 'Ford', 'model': 'Ecosport', 'vehicle_age': 2, 'km_driven': 10000, 'seller_type': 'Individual', 'fuel_type': 'Petrol', 'tran

NameError: name 'producer' is not defined

In [ ]:
# NOTE: For the Consumer programming, do not include the dataset portion. The rest works similar to the Producer codes but 
# change the serialization configurations to deserialiazation configurations.
